In [1]:
import os
import sys
import pandas as pd
import geopandas as gpd
import numpy as np
import pyproj
from matplotlib import pyplot as plt
import folium
import contextily as ctx

In [2]:
zdata1=r'C:\Project\FowlerPD&E_FloridaAve&56th\TBRPM_Fowler\ZDATA1_15A.dbf'
zdata2=r'C:\Project\FowlerPD&E_FloridaAve&56th\TBRPM_Fowler\ZDATA2_15A.dbf'
zdata1=gpd.read_file(zdata1)
zdata2=gpd.read_file(zdata2)

In [3]:
Fowler_TAZ=[167,168,303,304,305,306,307,308,309,310,311,312,313,314,315,318,319,320,
            321,322,323,324,175,176,177,178,179,180,181,182,183,184,185,325,326,330]

In [20]:
zdata_merge=zdata1.merge(zdata2,left_on='ZONE',right_on='ZONE')
# zdata_merge.set_index('ZONE',inplace=True)
# zdata_merge
zdata_merge_Fowler = zdata_merge.loc[zdata_merge.index[Fowler_TAZ]-1]
# zdata_merge_Fowler.head()
# for i in Fowler_TAZ:
#     DU=zdata_merge.loc[i-1,['DU','POP','TOT_EMP']]
#     print (DU);

In [21]:
Network=r'C:\Project\FowlerPD&E_FloridaAve&56th\TBRPM_Fowler\HWYLOAD_DAILY_A15.dbf'
Network=gpd.read_file(Network)[['A','B','AL_VOL','AL_VOL_T']]
# Network.head()

In [22]:
Volume_sum = Network.groupby(['A']).sum()

In [23]:
# print(Volume_sum.loc[[7]])#check row 7 only

In [24]:
zdata_volume=pd.merge(zdata_merge_Fowler,Volume_sum,left_on='ZONE',right_on='A')
# zdata_volume.head()

In [25]:
zdata_volume['Vol_DU']=(zdata_volume['AL_VOL_T']/zdata_volume['DU']).replace(np.inf, 0)
zdata_volume['Vol_POP']=(zdata_volume['AL_VOL_T']/zdata_volume['POP']).replace(np.inf, 0)
zdata_volume['Vol_EMP']=(zdata_volume['AL_VOL_T']/zdata_volume['TOT_EMP']).replace(np.inf, 0)
zdata_volume['Vol_DUEMP']=(zdata_volume['AL_VOL_T']/(zdata_volume['TOT_EMP']+zdata_volume['DU'])).replace(np.inf, 0)
# zdata_volume.head()

In [12]:
# zdata_volume.to_csv (r'C:\Project\FowlerPD&E_FloridaAve&56th\TBRPM_Fowler\zdata_volume_Fowler.csv', index = None, header=True) 

In [26]:
taz2015=r'C:\Project\FowlerPD&E_FloridaAve&56th\TBRPM_Fowler\TBRPMv9.0_TAZ_Shapefile\TBRPM_2017_TAZ_20181206.shp'
taz2015=gpd.read_file(taz2015)
# taz2015.head()
# ax=taz2015.plot(edgecolor='blue',linewidth=0.5,facecolor=(0,0,0,0))

In [27]:
taz15_fowler=taz2015.merge(zdata_volume,how='right',left_on='TAZ2015',right_on='ZONE')

In [28]:
HWYLOAD2015_link=r'C:\Project\FowlerPD&E_FloridaAve&56th\TBRPM_Fowler\HWYLOAD2015\HWYLOAD_DAILY_A15_FowlerLinkBuff.shp'
HWYLOAD2015=gpd.read_file(HWYLOAD2015_link)
HWYLOAD2015['TolVolCnt']=(HWYLOAD2015['AL_VOL_T']/HWYLOAD2015['PSWADT']).replace(np.inf, 0)
link=HWYLOAD2015.to_crs(epsg=4326)#convert to lat and long coordinate
link.index=link.LINK_ID
from branca import colormap


colormapper = colormap.linear.Purples_09.scale(
    t.Vol_DUEMP.min(),
    t.Vol_DUEMP.max(),
)
colormapper.caption='TAZ Generated Volume per DU&EMP'

# colormapper_link = colormap.linear.RdBu_09.scale(
#     link.AL_VOL_T.min(),
#     link.AL_VOL_T.max(),
# )
colormapper_link = colormap.LinearColormap(
    ['navy','blue','green','yellow','orange','red'],
    vmin=link.AL_VOL_T.min(), vmax=link.AL_VOL_T.max()
)
colormapper_link.caption='Total Volume'


# colormapper_volcnt = colormap.linear.Paired_06.scale(
#     link.TolVolCnt.min(),
#     link.TolVolCnt.max(),
# )

colormapper_volcnt = colormap.LinearColormap(
    ['navy','blue','green','yellow','orange','red'],
    vmin=link.TolVolCnt.min(), vmax=link.TolVolCnt.max()
)


colormapper_volcnt.caption='volume/count'

def vacant(x):
    if x==0:
        return "#faded1"
    else:
        return colormapper(x)
def vacant_link(x):
    if x==0:
        return "#faded1"
    else:
        return colormapper_link(x)
def vacant_volcnt(x):
    if x==0:
        return "gray"
    else:
        return colormapper_volcnt(x)
    
center=(28.04980,-82.41385)
m = folium.Map(center, zoom_start = 13,tiles=None)
folium.TileLayer('Stamen Toner', name='base map',overlay=True,opacity=0.3).add_to(m)
link_volcnt = folium.GeoJson(
    link,name='Volum/Count Layer',
    style_function=lambda feature: {
        'fillColor': vacant_volcnt(feature['properties']['TolVolCnt']),
        'color': 'black',
        'weight': 0.1,
        'fillOpacity': 1,
    },
    highlight_function=lambda feature: {
        'color': 'yellow',
        'weight': 4,
    },
    tooltip=folium.GeoJsonTooltip(
        fields=['TolVolCnt'],aliases=['Volume/Count'],localize=True,
    ),
).add_to(m)
link_s = folium.GeoJson(
    link,name='Total Volume Layer',
    style_function=lambda feature: {
        'fillColor': vacant_link(feature['properties']['AL_VOL_T']),
        'color': 'black',
        'weight': 0.1,
        'fillOpacity': 1,
    },
    highlight_function=lambda feature: {
        'color': 'cyan',
        'weight': 4,
    },
    tooltip=folium.GeoJsonTooltip(
        fields=['AL_VOL_T'],aliases=['2015 Bi-directional Volume'],localize=True,
    ),
).add_to(m)
taz_s = folium.GeoJson(
    t,name='TAZ Layer',
    style_function=lambda feature: {
        'fillColor': vacant(feature['properties']['Vol_DUEMP']),
        'color': 'black',
        'weight': 0.5,
        'fillOpacity': 0.8,
    },
    highlight_function=lambda feature: {
        'color': 'blue',
        'weight': 4,
    },
    tooltip=folium.GeoJsonTooltip(
        fields=['ZONE', 'AL_VOL_T', 'DU','TOT_EMP','Vol_DUEMP'],aliases=['ZONE', 'Bi-dir Volume', 'DU','EMP','Volume/(DU+EMP)'],localize=True,
    ),
).add_to(m)

colormapper.add_to(m)#this is to add the color legend to map
colormapper_volcnt.add_to(m)
m.keep_in_front(link_volcnt)
m.add_child(folium.map.LayerControl())
m


In [63]:
m.save(r'C:\Project\FowlerPD&E_FloridaAve&56th\TBRPM_Fowler\Fowler_2017VolumetoSEDataRatio.html')